In [365]:
import pandas as pd
import xlrd
import scipy
import numpy as np
from IPython.display import display
pd.options.display.max_columns = None
pd.options.display.max_rows = None
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
from sklearn import preprocessing

## Load and Clean Dataset

In [366]:
file = 'CaseStudy2data.xlsx'

# Load spreadsheet
xl = pd.ExcelFile(file)

# Load a sheet into a DataFrame by name: df1
attrition_df = xl.parse('HR-employee-attrition Data')

#drop unneccessary columns with constant values
attrition_column = attrition_df["Attrition"]
attrition_df.drop("Attrition", axis=1, inplace=True)
attrition_df.insert(0, "Attrition", attrition_column)
attrition_df.drop('EmployeeCount', axis=1, inplace=True)
attrition_df.drop('StandardHours', axis=1, inplace=True)
attrition_df.drop('Over18', axis=1, inplace=True)

#convert attrition variable to binary
attrition_df = attrition_df.replace("Yes", 1)
attrition_df = attrition_df.replace("No", 0)

# code dummy variables, this is necessary to use sklearn
attrition_df = pd.get_dummies(attrition_df, columns=["BusinessTravel", "Department", "EducationField", "Gender", "JobRole", "MaritalStatus"], prefix=["BusinessTravel", "Department", "EduationField", "Gender", "JobRole", "MaritalStatus"])
attrition_df

Attrition  Age  DailyRate  DistanceFromHome  Education  EmployeeNumber  \
0             1   41       1102                 1          2               1   
1             0   49        279                 8          1               2   
2             1   37       1373                 2          2               4   
3             0   33       1392                 3          4               5   
4             0   27        591                 2          1               7   
5             0   32       1005                 2          2               8   
6             0   59       1324                 3          3              10   
7             0   30       1358                24          1              11   
8             0   38        216                23          3              12   
9             0   36       1299                27          3              13   
10            0   35        809                16          3              14   
11            0   29        153                15          2              15   
12            0   31        670                26          1              16   
13            0   34       1346                19          2              18   
14            1   28        103                24          3              19   
15            0   29       1389                21          4              20   
16            0   32        334                 5          2              21   
17            0   22       1123                16          2              22   
18            0   53       1219                 2          4              23   
19            0   38        371                 2          3              24   
20            0   24        673                11          2              26   
21            1   36       1218                 9          4              27   
22            0   34        419                 7          4              28   
23            0   21        391                15          2              30   
24            1   34        699                 6          1              31   
25            0   53       1282                 5          3              32   
26            1   32       1125                16          1              33   
27            0   42        691                 8          4              35   
28            0   44        477                 7          4              36   
29            0   46        705                 2          4              38   
30            0   33        924                 2          3              39   
31            0   44       1459                10          4              40   
32            0   30        125                 9          2              41   
33            1   39        895                 5          3              42   
34            1   24        813                 1          3              45   
35            0   43       1273                 2          2              46   
36            1   50        869                 3          2              47   
37            0   35        890                 2          3              49   
38            0   36        852                 5          4              51   
39            0   33       1141                 1          3              52   
40            0   35        464                 4          2              53   
41            0   27       1240                 2          4              54   
42            1   26       1357                25          3              55   
43            0   27        994                 8          3              56   
44            0   30        721                 1          2              57   
45            1   41       1360                12          3              58   
46            0   34       1065                23          4              60   
47            0   37        408                19          2              61   
48            0   46       1211                 5          4              62   
49    

## Correlation Matrix to Identify Covariance

In [367]:
attrition_df.corr().abs()

Attrition       Age  DailyRate  \
Attrition                           1.000000  0.159205   0.056652   
Age                                 0.159205  1.000000   0.010661   
DailyRate                           0.056652  0.010661   1.000000   
DistanceFromHome                    0.077924  0.001686   0.004985   
Education                           0.031373  0.208034   0.016806   
EmployeeNumber                      0.010577  0.010145   0.050990   
EnvironmentSatisfaction             0.103369  0.010146   0.018355   
HourlyRate                          0.006846  0.024287   0.023381   
JobInvolvement                      0.130016  0.029820   0.046135   
JobLevel                            0.169105  0.509604   0.002966   
JobSatisfaction                     0.103481  0.004892   0.030571   
MonthlyIncome                       0.159840  0.497855   0.007707   
MonthlyRate                         0.015170  0.028051   0.032182   
NumCompaniesWorked                  0.043494  0.299635   0.038153   
OverTime                            0.246118  0.028062   0.009135   
PercentSalaryHike                   0.013478  0.003634   0.022704   
PerformanceRating                   0.002889  0.001904   0.000473   
RelationshipSatisfaction            0.045872  0.053535   0.007846   
StockOptionLevel                    0.137145  0.037510   0.042143   
TotalWorkingYears                   0.171063  0.680381   0.014515   
TrainingTimesLastYear               0.059478  0.019621   0.002453   
WorkLifeBalance                     0.063939  0.021490   0.037848   
YearsAtCompany                      0.134392  0.311309   0.034055   
YearsInCurrentRole                  0.160545  0.212901   0.009932   
YearsSinceLastPromotion             0.033019  0.216513   0.033229   
YearsWithCurrManager                0.156199  0.202089   0.026363   
BusinessTravel_Non-Travel           0.074457  0.011215   0.012096   
BusinessTravel_Travel_Frequently    0.115143  0.024743   0.011776   
BusinessTravel_Travel_Rarely        0.049538  0.028791   0.002078   
Department_Human Resources          0.016832  0.020523   0.026726   
Department_Research & Development   0.085293  0.017883   0.014871   
Department_Sales                    0.080855  0.027549   0.003616   
EduationField_Human Resources       0.036466  0.001696   0.043144   
EduationField_Life Sciences         0.032703  0.016824   0.004028   
EduationField_Marketing             0.055781  0.038162   0.064449   
EduationField_Medical               0.046999  0.006354   0.034202   
EduationField_Other                 0.017898  0.041466   0.003893   
EduationField_Technical Degree      0.069355  0.027604   0.030869   
Gender_Female                       0.029453  0.036311   0.011716   
Gender_Male                         0.029453  0.036311   0.011716   
JobRole_Healthcare Representative   0.078696  0.098825   0.040141   
JobRole_Human Resources             0.036215  0.029856   0.021156   
JobRole_Laboratory Technician       0.098290  0.143176   0.006728   
JobRole_Manager                     0.083316  0.294248   0.013224   
JobRole_Manufacturing Director      0.082994  0.049726   0.005302   
JobRole_Research Director           0.088870  0.185891   0.000021   
JobRole_Research Scientist          0.000360  0.146518   0.002624   
JobRole_Sales Executive             0.019774  0.002001   0.000513   
JobRole_Sales Representative        0.157234  0.175785   0.005375   
MaritalStatus_Divorced              0.087716  0.033120   0.037080   
MaritalStatus_Married               0.090984  0.083919   0.040035   
MaritalStatus_Single                0.175419  0.119185   0.075835   

                                   DistanceFromHome  Education  \
Attrition                                  0.077924   0.031373   
Age                                        0.001686   0.208034   
DailyRate                                  0.004985   0.016806   
DistanceFromHome                           1.000000   0.021042   
Education                                  0.02

Based off looking at the correlation matrix above, there are not any values that stand out as extremly correlated (0.8). Thus no variables will be removed.

## Chi-Square Univariate Selection

In [368]:
np.set_printoptions(precision=3)

values = attrition_df.values

X = values[:,1:(len(attrition_df.columns))]
Y = values[:,0]
number_of_featuers_to_select = 6

# feature extraction
test = SelectKBest(score_func=chi2, k=number_of_featuers_to_select).fit(X, Y)
test.transform(X)

# summarize scores
idxs = np.argsort(test.scores_)[:number_of_featuers_to_select]
scores = test.scores_[idxs]

# pvalues
idxs = np.argsort(test.pvalues_)[:number_of_featuers_to_select]
pvalues = test.pvalues_[idxs]

# feature names
idxs_selected = test.get_support(indices=True)
features = np.asarray(attrition_df.columns[idxs_selected])

# output features with their pvalues and score
print(list(zip(features, pvalues, scores)))


[('Age', 0.0, 0.0001523054445610236), ('JobSatisfaction', 3.2879327626280303e-262, 0.0005060644425394486), ('MonthlyIncome', 4.92392440516756e-210, 0.2350268575624977), ('StockOptionLevel', 4.149261818618412e-52, 0.39862638208752976), ('WorkLifeBalance', 9.247065655715055e-33, 0.4317790898209484), ('YearsAtCompany', 2.2057282778744752e-27, 0.4446056989443588)]


Based of Chi-Square analysis it seems that Age, JobSatisfaction, MonthlyIncome, StockOptionLevel, and WorkLifeBalance are the top factors the affect Attrition rate.